In [47]:
import pandas as pd
import numpy as np
from collections import Counter

import matplotlib.pyplot as plt
import matplotlib
import seaborn as sns

from sklearn import preprocessing

from sklearn.utils import shuffle
from sklearn.model_selection import GridSearchCV 
# from sklearn.model_selection import train_test_split
# from sklearn.model_selection import LeaveOneOut

from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import StackingClassifier

from sklearn import metrics

from scipy.stats import sem, t
from scipy import mean

#Oversampling
# from imblearn.over_sampling import RandomOverSampler
from kmeans_smote import KMeansSMOTE


### multiprocessing
from multiprocessing.pool import Pool


In [48]:
data = pd.read_csv('prepared Data.csv')
print(data.shape)
data.head()


(922, 33)


gender  age    SBP        BMI  etiology of CKD    Hb  Alb    Cr       eGFR  \
0       2   74  120.0  23.137669                2  12.0  4.0  1.20  89.981926   
1       1   57  139.0  28.515625                2  15.9  4.8  0.84  88.330020   
2       1   32  154.0  24.582701                4  14.4  4.4  0.87  86.973875   
3       1   60  144.0  30.737407                2  14.4  4.7  2.22  86.874201   
4       1   49  135.0  23.758726                2  17.0  4.1  1.39  86.782629   

   CKD_stage  ...   eGFR(6M)  eGFR(12M)  eGFR(18M)  eGFR(24M)  eGFR(30M)  \
0          3  ...  26.454698  24.331582  24.682189  21.614854  20.420524   
1          2  ...  78.287758  71.343858  72.845992  71.908942  71.562914   
2          2  ...  75.027238  69.595257  68.856399  72.901926  69.749275   
3          4  ...  26.885061  24.917353  28.581660  29.237135  25.556002   
4          3  ...  46.978867  45.829455  41.488436  41.801561  38.106104   

   eGFR(36M)  eGFR(last visit)  average_obs  obsevasion_ duration  fclass  
0  20.420524         18.495328    25.275139                    37       0  
1  67.225032         67.225032    72.392152                    37       0  
2  69.171408         69.171408    72.694258                    36       0  
3  25.183703         25.183703    26.485251                    35       0  
4  38.106104         38.106104    43.081581                    30       0  

[5 rows x 33 columns]

In [49]:
col = data.columns

In [50]:
count = Counter(data['fclass'])
count


Counter({0: 611, 1: 170, 5: 51, 2: 42, 6: 48})

# Feature Selection

In [51]:
# import pandas as pd
# import numpy as np
# data = pd.read_csv("D://Blogs//train.csv")
# X = data.iloc[:,0:20]  #independent columns
# y = data.iloc[:,-1]    #target column i.e price range
from sklearn.ensemble import ExtraTreesClassifier
importances = dict()
for col in data.iloc[:,:-1].columns:
    importances[col] = 0

for i in range(50):
    model = ExtraTreesClassifier()
    model.fit(data.iloc[:,:-1],data['fclass'])
    matplotlib.rcParams['figure.figsize'] = (8.0, 6.0)
    # print(model.feature_importances_) #use inbuilt class feature_importances of tree based classifiers
    #plot graph of feature importances for better visualization
    feat_importances = pd.Series(model.feature_importances_, index=data.iloc[:,:-1].columns)
    for col in data.iloc[:,:-1].columns:
        importances[col] += dict(feat_importances)[col]
#     feat_importances.nlargest(5).plot(kind='barh')
#     plt.show()
    
newpd = pd.DataFrame()
for col in data.iloc[:,:-1].columns:
    newpd[col] = list([importances[col]])
newpd.to_csv('feature_importamce.csv', index=False)

# Tuning

In [52]:
#preprocessing
max_abs_scaler = preprocessing.MaxAbsScaler()
X_train = max_abs_scaler.fit_transform(data.values[:,:-1])


kmeans_smote = KMeansSMOTE(
    kmeans_args={
        'n_clusters': 63
    },
    smote_args={
        'k_neighbors': 10
    })
X_train, y_train = kmeans_smote.fit_sample(X_train, data.values[:,-1])


/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.wa

In [ ]:
from sklearn.model_selection import GridSearchCV 
'Support Vector Machine'

# defining parameter range for SVM
param_grid = {'C': [0.1, 1, 10, 100, 1000],  
              'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
              'kernel': ['poly','rbf','sigmoid', 'linear']}  
  
grid = GridSearchCV(SVC(), param_grid, refit = True, verbose = 3, cv=5) 
 
# fitting the model for grid search 

grid.fit(X_train , y_train)
grid.best_params_

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Fitting 5 folds for each of 100 candidates, totalling 500 fits
[CV] C=0.1, gamma=1, kernel=poly .....................................
[CV] ......... C=0.1, gamma=1, kernel=poly, score=0.973, total=   0.7s
[CV] C=0.1, gamma=1, kernel=poly .....................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.7s remaining:    0.0s


[CV] ......... C=0.1, gamma=1, kernel=poly, score=0.973, total=   0.9s
[CV] C=0.1, gamma=1, kernel=poly .....................................


[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    1.6s remaining:    0.0s


[CV] ......... C=0.1, gamma=1, kernel=poly, score=0.985, total=   1.1s
[CV] C=0.1, gamma=1, kernel=poly .....................................
[CV] ......... C=0.1, gamma=1, kernel=poly, score=0.977, total=   0.9s
[CV] C=0.1, gamma=1, kernel=poly .....................................
[CV] ......... C=0.1, gamma=1, kernel=poly, score=0.965, total=   0.8s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.880, total=   2.4s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.924, total=   2.4s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.857, total=   2.7s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .......... C=0.1, gamma=1, kernel=rbf, score=0.849, total=   2.9s
[CV] C=0.1, gamma=1, kernel=rbf ......................................
[CV] .

In [12]:
from sklearn.model_selection import GridSearchCV 
'Support Vector Machine'

# defining parameter range for SVM
param_grid = {'C': [0.1, 1, 10, 100, 1000],  
              'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
              'kernel': ['poly','rbf','sigmoid']}  
  
grid = GridSearchCV(SVC(), param_grid, refit = True, verbose = 3, cv=5) 
 
# fitting the model for grid search 

grid.fit(X_train , y_train)
grid.best_params_

Fitting 5 folds for each of 25 candidates, totalling 125 fits
[CV] C=0.1, gamma=1, kernel=linear ...................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] ....... C=0.1, gamma=1, kernel=linear, score=0.773, total=   0.8s
[CV] C=0.1, gamma=1, kernel=linear ...................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.8s remaining:    0.0s


[CV] ....... C=0.1, gamma=1, kernel=linear, score=0.826, total=   0.7s
[CV] C=0.1, gamma=1, kernel=linear ...................................


...

[CV] ....... C=0.1, gamma=1, kernel=linear, score=0.677, total=   0.6s
[CV] C=0.1, gamma=1, kernel=linear ...................................
[CV] ....... C=0.1, gamma=1, kernel=linear, score=0.666, total=   0.6s
[CV] C=0.1, gamma=1, kernel=linear ...................................
[CV] ....... C=0.1, gamma=1, kernel=linear, score=0.694, total=   0.6s
[CV] C=0.1, gamma=0.1, kernel=linear .................................
[CV] ..... C=0.1, gamma=0.1, kernel=linear, score=0.773, total=   0.7s
[CV] C=0.1, gamma=0.1, kernel=linear .................................
[CV] ..... C=0.1, gamma=0.1, kernel=linear, score=0.826, total=   0.7s
[CV] C=0.1, gamma=0.1, kernel=linear .................................
[CV] ..... C=0.1, gamma=0.1, kernel=linear, score=0.677, total=   0.6s
[CV] C=0.1, gamma=0.1, kernel=linear .................................
[CV] ..... C=0.1, gamma=0.1, kernel=linear, score=0.666, total=   0.6s
[CV] C=0.1, gamma=0.1, kernel=linear .................................
[CV] .

[CV] ..... C=10, gamma=0.01, kernel=linear, score=0.834, total=   0.8s
[CV] C=10, gamma=0.01, kernel=linear .................................
[CV] ..... C=10, gamma=0.01, kernel=linear, score=0.876, total=   0.8s
[CV] C=10, gamma=0.01, kernel=linear .................................
[CV] ..... C=10, gamma=0.01, kernel=linear, score=0.798, total=   0.7s
[CV] C=10, gamma=0.01, kernel=linear .................................
[CV] ..... C=10, gamma=0.01, kernel=linear, score=0.791, total=   0.7s
[CV] C=10, gamma=0.01, kernel=linear .................................
[CV] ..... C=10, gamma=0.01, kernel=linear, score=0.808, total=   0.7s
[CV] C=10, gamma=0.001, kernel=linear ................................
[CV] .... C=10, gamma=0.001, kernel=linear, score=0.834, total=   0.7s
[CV] C=10, gamma=0.001, kernel=linear ................................
[CV] .... C=10, gamma=0.001, kernel=linear, score=0.876, total=   0.8s
[CV] C=10, gamma=0.001, kernel=linear ................................
[CV] .

[CV] .. C=1000, gamma=0.001, kernel=linear, score=0.865, total=  24.9s
[CV] C=1000, gamma=0.001, kernel=linear ..............................
[CV] .. C=1000, gamma=0.001, kernel=linear, score=0.863, total=  23.8s
[CV] C=1000, gamma=0.0001, kernel=linear .............................
[CV] . C=1000, gamma=0.0001, kernel=linear, score=0.859, total=  20.7s
[CV] C=1000, gamma=0.0001, kernel=linear .............................
[CV] . C=1000, gamma=0.0001, kernel=linear, score=0.899, total=  20.0s
[CV] C=1000, gamma=0.0001, kernel=linear .............................
[CV] . C=1000, gamma=0.0001, kernel=linear, score=0.861, total=  17.9s
[CV] C=1000, gamma=0.0001, kernel=linear .............................
[CV] . C=1000, gamma=0.0001, kernel=linear, score=0.865, total=  22.1s
[CV] C=1000, gamma=0.0001, kernel=linear .............................
[CV] . C=1000, gamma=0.0001, kernel=linear, score=0.863, total=  22.8s


[Parallel(n_jobs=1)]: Done 125 out of 125 | elapsed: 10.3min finished


{'C': 1000, 'gamma': 1, 'kernel': 'linear'}

In [ ]:
'Random Forest'
## Using grid search
rf = RandomForestClassifier()
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 4, 6, 8, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 3, 4]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}

grid = GridSearchCV(estimator = rf, param_grid = random_grid, refit = True, verbose = 3, cv=5) 
 
# fitting the model for grid search 
grid.fit(X_train , y_train)
grid.best_params_

Fitting 5 folds for each of 16800 candidates, totalling 84000 fits
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200 


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200, score=0.962, total=   2.3s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200 


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    2.3s remaining:    0.0s


[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200, score=0.963, total=   2.2s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=2, n_estimators=200 


...

[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=800, score=0.937, total=  11.8s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=800 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=800, score=0.923, total=  11.0s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=1000 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=1000, score=0.962, total=  13.7s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=1000 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4, n_estimators=1000, score=0.961, total=  13.2s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=4

[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200, score=0.960, total=   2.2s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200, score=0.924, total=   2.1s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200, score=0.931, total=   2.1s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=200, score=0.925, total=   2.1s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_

[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1400, score=0.925, total=  14.8s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600, score=0.961, total=  17.5s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600, score=0.959, total=  17.5s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=6, n_estimators=1600, score=0.919, total=  17.1s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_spli

[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=800, score=0.919, total=   8.5s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=800 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=800, score=0.925, total=   8.4s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=800 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=800, score=0.924, total=   8.4s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, n_estimators=1000, score=0.958, total=  10.9s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=8, 

[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200, score=0.960, total=   2.3s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200, score=0.955, total=   2.3s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200, score=0.919, total=   2.3s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200 
[CV]  bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_split=10, n_estimators=200, score=0.923, total=   2.3s
[CV] bootstrap=True, max_depth=10, max_features=auto, min_samples_leaf=1, min_samples_spli

In [10]:
'Gaussian Naive Bayes'

nb_classifier = GaussianNB()

params_NB = {'var_smoothing': np.logspace(0,-9, num=100)}
print(params_NB)

gs_NB = GridSearchCV(estimator=nb_classifier,
                 refit = True,
                 param_grid=params_NB, 
                 cv=5,  
                 verbose=3) 

gs_NB.fit(X_train, y_train)

gs_NB.best_params_

{'var_smoothing': array([1.00000000e+00, 8.11130831e-01, 6.57933225e-01, 5.33669923e-01,
       4.32876128e-01, 3.51119173e-01, 2.84803587e-01, 2.31012970e-01,
       1.87381742e-01, 1.51991108e-01, 1.23284674e-01, 1.00000000e-01,
       8.11130831e-02, 6.57933225e-02, 5.33669923e-02, 4.32876128e-02,
       3.51119173e-02, 2.84803587e-02, 2.31012970e-02, 1.87381742e-02,
       1.51991108e-02, 1.23284674e-02, 1.00000000e-02, 8.11130831e-03,
       6.57933225e-03, 5.33669923e-03, 4.32876128e-03, 3.51119173e-03,
       2.84803587e-03, 2.31012970e-03, 1.87381742e-03, 1.51991108e-03,
       1.23284674e-03, 1.00000000e-03, 8.11130831e-04, 6.57933225e-04,
       5.33669923e-04, 4.32876128e-04, 3.51119173e-04, 2.84803587e-04,
       2.31012970e-04, 1.87381742e-04, 1.51991108e-04, 1.23284674e-04,
       1.00000000e-04, 8.11130831e-05, 6.57933225e-05, 5.33669923e-05,
       4.32876128e-05, 3.51119173e-05, 2.84803587e-05, 2.31012970e-05,
       1.87381742e-05, 1.51991108e-05, 1.23284674e-05, 1.00

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


[CV] .... var_smoothing=0.2848035868435802, score=0.535, total=   0.0s
[CV] var_smoothing=0.2848035868435802 ................................
[CV] .... var_smoothing=0.2848035868435802, score=0.565, total=   0.0s
[CV] var_smoothing=0.2848035868435802 ................................
[CV] .... var_smoothing=0.2848035868435802, score=0.532, total=   0.0s
[CV] var_smoothing=0.23101297000831597 ...............................
[CV] ... var_smoothing=0.23101297000831597, score=0.556, total=   0.0s
[CV] var_smoothing=0.23101297000831597 ...............................
[CV] ... var_smoothing=0.23101297000831597, score=0.563, total=   0.0s
[CV] var_smoothing=0.23101297000831597 ...............................
[CV] ... var_smoothing=0.23101297000831597, score=0.544, total=   0.0s
[CV] var_smoothing=0.23101297000831597 ...............................
[CV] ... var_smoothing=0.23101297000831597, score=0.570, total=   0.0s
[CV] var_smoothing=0.23101297000831597 ...............................
[CV] .

[CV] ... var_smoothing=0.01873817422860384, score=0.568, total=   0.0s
[CV] var_smoothing=0.01873817422860384 ...............................
[CV] ... var_smoothing=0.01873817422860384, score=0.558, total=   0.0s
[CV] var_smoothing=0.01873817422860384 ...............................
[CV] ... var_smoothing=0.01873817422860384, score=0.586, total=   0.0s
[CV] var_smoothing=0.01873817422860384 ...............................
[CV] ... var_smoothing=0.01873817422860384, score=0.547, total=   0.0s
[CV] var_smoothing=0.01519911082952933 ...............................
[CV] ... var_smoothing=0.01519911082952933, score=0.571, total=   0.0s
[CV] var_smoothing=0.01519911082952933 ...............................
[CV] ... var_smoothing=0.01519911082952933, score=0.569, total=   0.0s
[CV] var_smoothing=0.01519911082952933 ...............................
[CV] ... var_smoothing=0.01519911082952933, score=0.563, total=   0.0s
[CV] var_smoothing=0.01519911082952933 ...............................
[CV] .

[CV] . var_smoothing=0.0012328467394420659, score=0.581, total=   0.0s
[CV] var_smoothing=0.0012328467394420659 .............................
[CV] . var_smoothing=0.0012328467394420659, score=0.586, total=   0.0s
[CV] var_smoothing=0.0012328467394420659 .............................
[CV] . var_smoothing=0.0012328467394420659, score=0.576, total=   0.0s
[CV] var_smoothing=0.001 .............................................
[CV] ................. var_smoothing=0.001, score=0.597, total=   0.0s
[CV] var_smoothing=0.001 .............................................
[CV] ................. var_smoothing=0.001, score=0.591, total=   0.0s
[CV] var_smoothing=0.001 .............................................
[CV] ................. var_smoothing=0.001, score=0.580, total=   0.0s
[CV] var_smoothing=0.001 .............................................
[CV] ................. var_smoothing=0.001, score=0.585, total=   0.0s
[CV] var_smoothing=0.001 .............................................
[CV] .

...

[CV] . var_smoothing=2.848035868435799e-06, score=0.570, total=   0.0s
[CV] var_smoothing=2.848035868435799e-06 .............................
[CV] . var_smoothing=2.848035868435799e-06, score=0.564, total=   0.0s
[CV] var_smoothing=2.310129700083158e-06 .............................
[CV] . var_smoothing=2.310129700083158e-06, score=0.587, total=   0.0s
[CV] var_smoothing=2.310129700083158e-06 .............................
[CV] . var_smoothing=2.310129700083158e-06, score=0.587, total=   0.0s
[CV] var_smoothing=2.310129700083158e-06 .............................
[CV] . var_smoothing=2.310129700083158e-06, score=0.567, total=   0.0s
[CV] var_smoothing=2.310129700083158e-06 .............................
[CV] . var_smoothing=2.310129700083158e-06, score=0.570, total=   0.0s
[CV] var_smoothing=2.310129700083158e-06 .............................
[CV] . var_smoothing=2.310129700083158e-06, score=0.564, total=   0.0s
[CV] var_smoothing=1.873817422860383e-06 .............................
[CV] .

[CV] ................. var_smoothing=1e-07, score=0.559, total=   0.0s
[CV] var_smoothing=1e-07 .............................................
[CV] ................. var_smoothing=1e-07, score=0.559, total=   0.0s
[CV] var_smoothing=1e-07 .............................................
[CV] ................. var_smoothing=1e-07, score=0.562, total=   0.0s
[CV] var_smoothing=8.111308307896873e-08 .............................
[CV] . var_smoothing=8.111308307896873e-08, score=0.575, total=   0.0s
[CV] var_smoothing=8.111308307896873e-08 .............................
[CV] . var_smoothing=8.111308307896873e-08, score=0.585, total=   0.0s
[CV] var_smoothing=8.111308307896873e-08 .............................
[CV] . var_smoothing=8.111308307896873e-08, score=0.559, total=   0.0s
[CV] var_smoothing=8.111308307896873e-08 .............................
[CV] . var_smoothing=8.111308307896873e-08, score=0.558, total=   0.0s
[CV] var_smoothing=8.111308307896873e-08 .............................
[CV] .

[CV] . var_smoothing=2.310129700083158e-09, score=0.578, total=   0.0s
[CV] var_smoothing=2.310129700083158e-09 .............................
[CV] . var_smoothing=2.310129700083158e-09, score=0.551, total=   0.0s
[CV] var_smoothing=2.310129700083158e-09 .............................
[CV] . var_smoothing=2.310129700083158e-09, score=0.553, total=   0.0s
[CV] var_smoothing=2.310129700083158e-09 .............................
[CV] . var_smoothing=2.310129700083158e-09, score=0.553, total=   0.0s
[CV] var_smoothing=1.873817422860387e-09 .............................
[CV] . var_smoothing=1.873817422860387e-09, score=0.568, total=   0.0s
[CV] var_smoothing=1.873817422860387e-09 .............................
[CV] . var_smoothing=1.873817422860387e-09, score=0.578, total=   0.0s
[CV] var_smoothing=1.873817422860387e-09 .............................
[CV] . var_smoothing=1.873817422860387e-09, score=0.552, total=   0.0s
[CV] var_smoothing=1.873817422860387e-09 .............................
[CV] .

[Parallel(n_jobs=1)]: Done 500 out of 500 | elapsed:    3.4s finished


{'var_smoothing': 0.0008111308307896872}

In [34]:
'Linear Discriminant Analysis'
from numpy import arange
# define grid
grid = dict()
grid['solver'] = ['svd', 'lsqr', 'eigen']
# grid['shrinkage'] = arange(0, 1, 0.01)
# define model
model = LinearDiscriminantAnalysis()
LDA_search = GridSearchCV(model, grid,
                 refit = True,
                 cv=5,  
                 verbose=3) 
LDA_search.fit(X_train, y_train)
# summarize
print('Mean Accuracy: %.3f' % LDA_search.best_score_)
print('Config: %s' % LDA_search.best_params_)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
[CV] solver=svd ......................................................
[CV] .......................... solver=svd, score=0.739, total=   0.0s
[CV] solver=svd ......................................................
[CV] .......................... solver=svd, score=0.731, total=   0.1s
[CV] solver=svd ......................................................
[CV] .......................... solver=svd, score=0.716, total=   0.1s
[CV] solver=svd ......................................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s


[CV] .......................... solver=svd, score=0.726, total=   0.1s
[CV] solver=svd ......................................................
[CV] .......................... solver=svd, score=0.694, total=   0.1s
[CV] solver=lsqr .....................................................
[CV] ......................... solver=lsqr, score=0.739, total=   0.0s
[CV] solver=lsqr .....................................................
[CV] ......................... solver=lsqr, score=0.731, total=   0.0s
[CV] solver=lsqr .....................................................
[CV] ......................... solver=lsqr, score=0.716, total=   0.0s
[CV] solver=lsqr .....................................................
[CV] ......................... solver=lsqr, score=0.726, total=   0.0s
[CV] solver=lsqr .....................................................
[CV] ......................... solver=lsqr, score=0.694, total=   0.0s
[CV] solver=eigen ....................................................
[CV] .

/home/amin/.local/lib/python3.6/site-packages/sklearn/model_selection/_validation.py:552: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "/home/amin/.local/lib/python3.6/site-packages/sklearn/model_selection/_validation.py", line 531, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/amin/.local/lib/python3.6/site-packages/sklearn/discriminant_analysis.py", line 468, in fit
    self._solve_eigen(X, y, shrinkage=self.shrinkage)
  File "/home/amin/.local/lib/python3.6/site-packages/sklearn/discriminant_analysis.py", line 335, in _solve_eigen
    evals, evecs = linalg.eigh(Sb, Sw)
  File "/home/amin/.local/lib/python3.6/site-packages/scipy/linalg/decomp.py", line 581, in eigh
    'or eigenvectors were computed.'.format(info-n))
numpy.linalg.LinAlgError: The leading minor of order 30 of B is not positive definite. The factorization of 

[CV] ........................ solver=eigen, score=0.694, total=   0.1s
Mean Accuracy: 0.721
Config: {'solver': 'svd'}


In [ ]:
'Decision Tree'
DT = DecisionTreeClassifier()

criterion = ['gini', 'entropy']
max_depth =  list(range(10, 60, 5))
max_features = list(range(1 ,X_train.shape[1]))
min_samples_leaf = list(range(1, 31, 3))
min_samples_split = list(range(2, 10, 2))
presort = [False, True]

DT_param = {'criterion': criterion,
               'max_depth': max_depth,
               'max_features': max_features,
               'min_samples_leaf': min_samples_leaf,
               'min_samples_split': min_samples_split}

DT_grid = GridSearchCV(estimator = DT, param_grid = DT_param, refit = True, verbose = 3, cv=5) 
# fitting the model for grid search 
DT_grid.fit(X_train , y_train)
DT_grid.best_params_
# summarize
print('Mean Accuracy: %.3f' % DT_grid.best_score_)
print('Config: %s' % DT_grid.best_params_)

Fitting 5 folds for each of 24800 candidates, totalling 124000 fits
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, score=0.768, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, score=0.769, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, score=0.759, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_split=2, score=0.697, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=1, min_samples_s

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s


[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=2, score=0.684, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=2 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=2, score=0.676, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4, score=0.723, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4, score=0.755, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=4, min_samples_split=4, score=0.692, total=   0.0s
[CV] criterion=gini, max_depth=1

[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=6, score=0.625, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8, score=0.630, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8, score=0.717, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8, score=0.683, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=10, min_samples_split=8, score=0.707, total=   0.0s
[CV] criterion=gini, ma

[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=4, score=0.664, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6, score=0.693, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6, score=0.714, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6, score=0.653, total=   0.0s
[CV] criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6 
[CV]  criterion=gini, max_depth=10, max_features=1, min_samples_leaf=19, min_samples_split=6, score=0.691, total=   0.0s
[CV] criterion=gini, ma

...

[CV]  criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=2, score=0.802, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=2, score=0.803, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4 
[CV]  criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4, score=0.854, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4 
[CV]  criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4, score=0.849, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4 
[CV]  criterion=gini, max_depth=25, max_features=17, min_samples_leaf=25, min_samples_split=4, score=0.833, total=   0.1s
[CV] criterion

[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2, score=0.925, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2, score=0.911, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2, score=0.904, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=2, score=0.916, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=4 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=1, min_samples_split=4, score=0.918, total=   0.2s
[CV] criterion=gini, ma

[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2, score=0.885, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2, score=0.909, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2, score=0.892, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2, score=0.849, total=   0.2s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=7, min_samples_split=2, score=0.879, total=   0.2s
[CV] criterion=gini, ma

[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2, score=0.867, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2, score=0.882, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2, score=0.847, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2, score=0.829, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=13, min_samples_split=2, score=0.843, total=   0.1s
[CV] criterion

[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2, score=0.836, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2, score=0.851, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2, score=0.835, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2, score=0.822, total=   0.1s
[CV] criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2 
[CV]  criterion=gini, max_depth=25, max_features=18, min_samples_leaf=19, min_samples_split=2, score=0.834, total=   0.1s
[CV] criterion

In [ ]:
# summarize
print('Mean Accuracy: %.3f' % DT_grid.best_score_)
print('Config: %s' % DT_grid.best_params_)

In [147]:
'Logistic Regression'
LR = LogisticRegression()
LRparam_grid = {
    'C': [0.001, 0.01, 0.1, 1, 10, 100, 1000],
    'penalty': ['l1', 'l2'],
    'max_iter': list(range(100,800,100)),
    'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga']
}
LR_search = GridSearchCV(LR, param_grid=LRparam_grid, refit = True, verbose = 3, cv=5)

# fitting the model for grid search 
LR_search.fit(X_train , y_train)
LR_search.best_params_
# summarize
print('Mean Accuracy: %.3f' % LR_search.best_score_)
print('Config: %s' % LR_search.best_params_)

In [148]:
'K Neighbors Classifier'
  
# # defining parameter range for SVM
# param_grid = {'C': [0.1, 1, 10, 100, 1000],  
#               'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
#               'kernel': ['poly','rbf','sigmoid']}  
  
# grid = GridSearchCV(SVC(), param_grid, refit = True, verbose = 3) 
  
# # fitting the model for grid search 
# grid.fit(data.values[:,:-1], data.values[:,-1]) 

In [150]:
'Gradient Boosting'
  
# # defining parameter range for SVM
# param_grid = {'C': [0.1, 1, 10, 100, 1000],  
#               'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
#               'kernel': ['poly','rbf','sigmoid']}  
  
# grid = GridSearchCV(SVC(), param_grid, refit = True, verbose = 3) 
  
# # fitting the model for grid search 
# grid.fit(data.values[:,:-1], data.values[:,-1]) 

# Oversampling

In [151]:
# X, y = data.values[:int(800),:-1], data.values[:int(800),-1]
# [print('Class {} has {} instances'.format(label, count))
#  for label, count in zip(*np.unique(y, return_counts=True))]

# kmeans_smote = KMeansSMOTE(
#     kmeans_args={
#         'n_clusters': 63
#     },
#     smote_args={
#         'k_neighbors': 10
#     }
# )
# X_resampled, y_resampled = kmeans_smote.fit_sample(X, y)

# [print('Class {} has {} instances after oversampling'.format(label, count))
#  for label, count in zip(*np.unique(y_resampled, return_counts=True))]
# print(Counter(y_resampled))

In [152]:
# define oversampling strategy
# oversample = RandomOverSampler(sampling_strategy='minority')

## Below code works for binary classification 
# oversample = RandomOverSampler(sampling_strategy=0.5)

In [153]:

# # define oversampling strategy
# oversample = RandomOverSampler(sampling_strategy='minority')

# # fit and apply the transform
# X_over, y_over = oversample.fit_resample(data.values[:,:-1], data.values[:,-1])

# Max = dict(Counter(y_over))[0.0]
# flag = True
# while flag:
#     X_over, y_over = oversample.fit_resample(X_over, y_over)
#     for x in list(dict(Counter(y_over)).values()):
#         if x == Max:
#             flag = False
#         else:
#             flag = True
#             break
        
# # summarize class distribution
# print(Counter(y_over))

In [154]:
# adict = dict()
# adict.update(zip(d.columns,col[:-1]))
# adict

In [155]:
# d = pd.DataFrame(X_over)
# adict = dict()
# adict.update(zip(d.columns,col[:-1]))
# d.rename(columns = adict, inplace =True)
# d['fclass'] = y_over
# d.head()

In [156]:
# count = Counter(data['fclass'])
# count

In [157]:
# data = d.copy()

In [7]:
cat0 = shuffle(data[data['fclass']==0])
cat1 = shuffle(data[data['fclass']==1])
cat2 = shuffle(data[data['fclass']==2])
cat5 = shuffle(data[data['fclass']==5])
cat6 = shuffle(data[data['fclass']==6])



lenCat0 = len(cat0.iloc[:,0])
lenCat1 = len(cat1.iloc[:,0])
lenCat2 = len(cat2.iloc[:,0])
lenCat5 = len(cat5.iloc[:,0])
lenCat6 = len(cat6.iloc[:,0])


In [9]:
methodList = []
accRes = []
accConf = []
nFold = 10
# sensitivityList = []
# specificityList = []

In [10]:
basicMethods = ['Gradient Boosting','Support Vector Machine', 'Logistic Regression', 'K Neighbors Classifier',\
                'Random Forest', 'Gaussian Naive Bayes', 'Linear Discriminant Analysis', 'Decision Tree']

methods = ['stacking classifir', 'soft votingClassifier','hard votingClassifier', 'Gradient Boosting',\
           'Support Vector Machine', 'Logistic Regression', 'K Neighbors Classifier', 'Random Forest',\
           'Gaussian Naive Bayes', 'Linear Discriminant Analysis', 'Decision Tree']
# methods = ['hard votingClassifier']

In [11]:
## 10 fold-CV

def classifiers(method):
    cl1 = LogisticRegression(solver='lbfgs', max_iter=500)
    cl2 = KNeighborsClassifier(n_neighbors=10)
    cl3 = RandomForestClassifier(max_depth=50)
    cl4 = GaussianNB()
    cl5 = LinearDiscriminantAnalysis()
    cl6 = DecisionTreeClassifier()
    cl7 = SVC(C=100, gamma=1, kernel='rbf',probability=True)
    cl8 = GradientBoostingClassifier()
    estimator = [(basicMethods[0],cl1), (basicMethods[1],cl2), (basicMethods[2],cl3),\
                 (basicMethods[3],cl4), (basicMethods[4],cl5), (basicMethods[5],cl6),\
                 (basicMethods[6],cl7), (basicMethods[7],cl8)]
    
    if method == 'Logistic Regression':
        CL = LogisticRegression(solver='lbfgs', max_iter=500)
        
    if method == 'K Neighbors Classifier':
        CL = KNeighborsClassifier(n_neighbors=10)
        
    if method == 'Random Forest':
        CL = RandomForestClassifier(max_depth=50)
        
    if method == 'Gaussian Naive Bayes':
        CL = GaussianNB()
        
    if method == 'Linear Discriminant Analysis':
        CL = LinearDiscriminantAnalysis()
        
    if method == 'Decision Tree':
        CL = DecisionTreeClassifier()
        
    if method == 'Support Vector Machine':
        CL = SVC(C=100, gamma=1, kernel='rbf',probability=True)
#         class_weight='balanced', C=1.0

    if method == 'Gradient Boosting':
        CL = GradientBoostingClassifier()
        
    if method == 'soft votingClassifier':
        CL = VotingClassifier(estimators=estimator, voting='soft', weights=[10, 3, 6, 5, 10, 5, 6, 8])
        
    if method == 'hard votingClassifier':
        CL = VotingClassifier(estimators=estimator, voting='hard')
    
    if method == 'stacking classifir':
        CL = StackingClassifier(estimators=estimator, final_estimator=cl1, cv=5)
    print(type(CL))
    accList = []
    for j in range(nFold):

        i = j*.1
        k = (j+1)*.1
        #train
        X_train = cat0.iloc[int(k * lenCat0):,:-1].append(\
                  cat1.iloc[int(k * lenCat1):,:-1].append(\
                  cat2.iloc[int(k * lenCat2):,:-1].append(\
                  cat5.iloc[int(k * lenCat5):,:-1].append(\
                  cat6.iloc[int(k * lenCat6):,:-1].append(\
                  cat0.iloc[:int(i * lenCat0),:-1].append(\
                  cat1.iloc[:int(i * lenCat1),:-1].append(\
                  cat2.iloc[:int(i * lenCat2),:-1].append(\
                  cat5.iloc[:int(i * lenCat5),:-1].append(\
                  cat6.iloc[:int(i * lenCat6),:-1]                                       
                                                         )))))))))

        y_train = cat0.iloc[int(k * lenCat0):,-1].append(\
                  cat1.iloc[int(k * lenCat1):,-1].append(\
                  cat2.iloc[int(k * lenCat2):,-1].append(\
                  cat5.iloc[int(k * lenCat5):,-1].append(\
                  cat6.iloc[int(k * lenCat6):,-1].append(\
                  cat0.iloc[:int(i * lenCat0),-1].append(\
                  cat1.iloc[:int(i * lenCat1),-1].append(\
                  cat2.iloc[:int(i * lenCat2),-1].append(\
                  cat5.iloc[:int(i * lenCat5),-1].append(\
                  cat6.iloc[:int(i * lenCat6),-1]                                         
                                                        )))))))))
#         print(X_train.shape, y_train.shape)


        #preprocessing
        max_abs_scaler = preprocessing.MaxAbsScaler()
        X_train = max_abs_scaler.fit_transform(X_train)
        
        scaler = preprocessing.StandardScaler()
#         X_train = scaler.fit_transform(X_train)
 

        # fit and apply the Oversampling:
        #### Repeatitive oversampling
#         X_over, y_over = oversample.fit_resample(X_train, y_train)

#         Max = dict(Counter(y_over))[0.0]
#         flag = True
#         while flag:
#             X_over, y_over = oversample.fit_resample(X_over, y_over)
#             for x in list(dict(Counter(y_over)).values()):
#                 if x == Max:
#                     flag = False
#                 else:
#                     flag = True
#                     break
#         X_train, y_train = X_over.copy(), y_over.copy()
        # summarize class distribution
#         print(Counter(y_train))

#         print(X_train.shape, y_train.shape)
    

        # fit and apply the Oversampling:
        #### K-means oversampling
#         [print('Class {} has {} instances'.format(label, count))
#          for label, count in zip(*np.unique(y, return_counts=True))]

        kmeans_smote = KMeansSMOTE(
            kmeans_args={
                'n_clusters': 63
            },
            smote_args={
                'k_neighbors': 10
            }
        )
        X_train, y_train = kmeans_smote.fit_sample(X_train, y_train)

#         [print('Class {} has {} instances after oversampling'.format(label, count))
#          for label, count in zip(*np.unique(y_resampled, return_counts=True))]
        # summarize class distribution
#         print(Counter(y_train))

        #test
        X_test = cat0.iloc[int(i * lenCat0):int(k * lenCat0),:-1].append(\
                 cat1.iloc[int(i * lenCat1):int(k * lenCat1),:-1].append(\
                 cat2.iloc[int(i * lenCat2):int(k * lenCat2),:-1].append(\
                 cat5.iloc[int(i * lenCat5):int(k * lenCat5),:-1].append(\
                 cat6.iloc[int(i * lenCat6):int(k * lenCat6),:-1]))))

        y_test = cat0.iloc[int(i * lenCat0):int(k * lenCat0),-1].append(\
                 cat1.iloc[int(i * lenCat1):int(k * lenCat1),-1].append(\
                 cat2.iloc[int(i * lenCat2):int(k * lenCat2),-1].append(\
                 cat5.iloc[int(i * lenCat5):int(k * lenCat5),-1].append(\
                 cat6.iloc[int(i * lenCat6):int(k * lenCat6),-1]))))
#         print(X_test.shape, y_test.shape)
        X_test = max_abs_scaler.transform(X_test)
#         X_test = scaler.transform(X_test)   
        
        model = CL.fit(X_train, np.array(list(y_train)))
        
        predict = np.array(model.predict(X_test))
        
        cnf_matrix = metrics.confusion_matrix(y_test, predict)
        print(method)
        print(cnf_matrix)
#         #matplotlib inline
#         class_names=[0,1] # name  of classes
#         fig, ax = plt.subplots()
#         tick_marks = np.arange(len(class_names))
#         plt.xticks(tick_marks, class_names)
#         plt.yticks(tick_marks, class_names)

#         # create heatmap
#         sns.heatmap(pd.DataFrame(cnf_matrix), annot=True, cmap="YlGnBu" ,fmt='g')
#         ax.xaxis.set_label_position("top")
#         plt.tight_layout()
#         plt.title(method+ ' fold of '+str(j), y=1.1)

#         plt.ylabel('Actual label')
#         plt.xlabel('Predicted label')

#         plt.show()


        acc = metrics.accuracy_score(y_test.values, predict)
        accList.append(acc)


    methodList.append(method)
    confidence = 0.95

    naccList = len(accList)
    maccList = np.mean(accList)
    std_erraccList = sem(accList)
    haccList = std_erraccList * t.ppf((1 + confidence) / 2, naccList - 1)




    print("Accuracy:         "+ str(round(maccList,2)) + '  -+' + str(round(haccList,4)))
    accRes.append(round(maccList,2))
    accConf.append(round(haccList,4))
    return (method, round(maccList,2), round(haccList,4))


In [12]:
if __name__ == "__main__":
    p = Pool(processes=7)
    result1 = p.map(classifiers, methods)
    p.close()
    p.join()

<class 'sklearn.ensemble._voting.VotingClassifier'><class 'sklearn.ensemble._voting.VotingClassifier'><class 'sklearn.svm._classes.SVC'><class 'sklearn.ensemble._stacking.StackingClassifier'><class 'sklearn.ensemble._gb.GradientBoostingClassifier'><class 'sklearn.linear_model._logistic.LogisticRegression'><class 'sklearn.neighbors._classification.KNeighborsClassifier'>








/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.wa

/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.wa

/home/amin/.local/lib/python3.6/site-packages/kmeans_smote.py:322: UserWarning: No minority clusters found for class 5. Performing regular SMOTE. Try changing the number of clusters.
  warnings.warn('No minority clusters found for class {}. Performing regular SMOTE. Try changing the number of clusters.'.format(minority_class_label))
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is 

/home/amin/.local/lib/python3.6/site-packages/kmeans_smote.py:322: UserWarning: No minority clusters found for class 5. Performing regular SMOTE. Try changing the number of clusters.
  warnings.warn('No minority clusters found for class {}. Performing regular SMOTE. Try changing the number of clusters.'.format(minority_class_label))
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/kmeans_smote.py:322: UserWarning: No minority clusters found for class 6. Performing regular SMOTE. Try

...

stacking classifir
[[58  1  0  2  0]
 [ 3 14  0  0  0]
 [ 4  0  0  0  0]
 [ 5  0  0  0  0]
 [ 1  2  0  0  2]]


/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/kmeans_smote.py:322: UserWarning: No minority clusters found for class 2. Performing regular SMOTE. Try changing the number of clusters.
  warnings.warn('No minority clusters found

stacking classifir
[[56  2  2  1  0]
 [ 0 16  0  0  1]
 [ 2  0  1  0  1]
 [ 5  0  0  0  0]
 [ 2  3  0  0  0]]


/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is deprecated in version 0.22 and will be removed in version 0.24.
  warnings.warn(msg, category=FutureWarning)
/home/amin/.local/lib/python3.6/site-packages/kmeans_smote.py:322: UserWarning: No minority clusters found for class 2. Performing regular SMOTE. Try changing the number of clusters.
  warnings.warn('No minority clusters found for class {}. Performing regular SMOTE. Try changing the number of clusters.'.format(minority_class_label))
/home/amin/.local/lib/python3.6/site-packages/sklearn/utils/deprecation.py:86: FutureWarning: Function safe_indexing is deprecated; safe_indexing is 

stacking classifir
[[57  1  1  2  1]
 [ 4 11  0  0  2]
 [ 5  0  0  0  0]
 [ 5  0  1  0  0]
 [ 0  4  1  0  0]]
Accuracy:         0.78  -+0.0218


In [13]:
result = pd.DataFrame(result1)
result.columns = ['Method','Accuracy','ACC CI']

In [14]:
result

Method  Accuracy  ACC CI
0             stacking classifir      0.78  0.0218
1          soft votingClassifier      0.64  0.0174
2          hard votingClassifier      0.67  0.0202
3              Gradient Boosting      0.73  0.0293
4         Support Vector Machine      0.66  0.0242
5            Logistic Regression      0.48  0.0426
6         K Neighbors Classifier      0.42  0.0303
7                  Random Forest      0.75  0.0326
8           Gaussian Naive Bayes      0.41  0.0403
9   Linear Discriminant Analysis      0.48  0.0341
10                 Decision Tree      0.63  0.0336

In [15]:
# # result = []
# result = pd.DataFrame(result1)
# result['Method'],result['Accuracy'],result['ACC CI'] = methodList,accRes,accConf
result.to_excel('kidney_Classification_Result_preprocess before oversampling.xlsx',index=False)
result

Method  Accuracy  ACC CI
0             stacking classifir      0.78  0.0218
1          soft votingClassifier      0.64  0.0174
2          hard votingClassifier      0.67  0.0202
3              Gradient Boosting      0.73  0.0293
4         Support Vector Machine      0.66  0.0242
5            Logistic Regression      0.48  0.0426
6         K Neighbors Classifier      0.42  0.0303
7                  Random Forest      0.75  0.0326
8           Gaussian Naive Bayes      0.41  0.0403
9   Linear Discriminant Analysis      0.48  0.0341
10                 Decision Tree      0.63  0.0336